# 한동대학교 학사 규정집 기반의 RAG 구현 해커톤

2024년 5월 16일
최명진

web scraper를 이용하여 한동대학교 규정집 https://rule.hangond.edu 을 모두 다운로드 받았다.

1. 파일을 임베딩해서 벡터 디비에 넣는다
2. 질의에 대한 응답을 찾기 위해서 벡터 디비에서 유사 문서를 가져와서 생성한다.


In [58]:
import re
import os
import builtins

def extract_and_save_html_content(file_path):
    print(f"파일 경로: {file_path}")
    # 파일 열기
    with builtins.open(file_path, 'r', encoding='UTF-8') as file:
        content = file.read()    
        # 정규식 패턴에 맞는 문자열 추출
        pattern = r'< .*&nbsp;&nbsp;&nbsp;\|'
        extracted_content = re.findall(pattern, content).pop().replace('&nbsp;&nbsp;&nbsp;|', '')[2:].split(" < ")

        print(f"추출된 내용: {extracted_content}")

        # 배열에서 파일명과 폴더 경로 분리
        file_name = extracted_content[-1] + ".html"
        folder_path = "rules/" + os.path.join(*extracted_content[:-1])

        # 폴더 경로가 존재하지 않으면 생성
        if not os.path.exists(folder_path):
            os.makedirs(folder_path)

        # 전체 파일 경로 생성
        file_path = os.path.join(folder_path, file_name)

        # 파일에 내용 쓰기
        with open(file_path, 'w') as file:
            file.write(content)
            
        print(f"File saved at: {file_path}")

In [59]:
# rename the file
import os
# sample_data 폴더의 경로를 지정합니다.
sample_data_path = './data/'

# sample_data 폴더에 있는 모든 파일 중에서 HTML 확장자를 가진 파일을 찾습니다.
html_files = [f for f in os.listdir(sample_data_path) if f.endswith('.html')]

docs = []
# HTML 파일 목록을 출력합니다.
print("HTML 파일 목록 (상대 경로):")
for html_file in html_files:
  try:
    relative_path = os.path.join('data', html_file)
    print(relative_path)
    extract_and_save_html_content(relative_path)

    # html_data = reader.load_data(relative_path)
    # print(html_data)
    # docs.append(html_data)
  except Exception as e:
    print("Somthng wrong")
    traceback.print_exc()

HTML 파일 목록 (상대 경로):
data/Gku (95).html
파일 경로: data/Gku (95).html
추출된 내용: ['본부,부속기관 및 부속 연구소', '본부 및 부속 기관', '결혼·다출산문화운동센터 운영규정']
File saved at: rules/본부,부속기관 및 부속 연구소/본부 및 부속 기관/결혼·다출산문화운동센터 운영규정.html
data/Gku (68).html
파일 경로: data/Gku (68).html
추출된 내용: ['행정', '학생 행정', '학생단체등록과 활동에 관한 규정']
File saved at: rules/행정/학생 행정/학생단체등록과 활동에 관한 규정.html
data/Gku - 2024-05-16T100841.351.html
파일 경로: data/Gku - 2024-05-16T100841.351.html
추출된 내용: ['세칙', '강사 인사관리 세칙']
File saved at: rules/세칙/강사 인사관리 세칙.html
data/Gku (10).html
파일 경로: data/Gku (10).html
추출된 내용: ['행정', '일반 행정', '환경관리규정']
File saved at: rules/행정/일반 행정/환경관리규정.html
data/Gku (55).html
파일 경로: data/Gku (55).html
추출된 내용: ['행정', '교무·연구 행정', '학사운영규정']
File saved at: rules/행정/교무·연구 행정/학사운영규정.html
data/Gku - 2024-05-16T100841.412.html
파일 경로: data/Gku - 2024-05-16T100841.412.html
추출된 내용: ['세칙', '교환학생 학점 인정에 관한 세칙']
File saved at: rules/세칙/교환학생 학점 인정에 관한 세칙.html
data/Gku (34).html
파일 경로: data/Gku (34).html
추출된 내용: ['행정', '인사 행정', '교원담당시간수및강의료지급규정']
Fi

In [63]:
import os


def generate_index_html(directory):
    # HTML header and footer
    header = """<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>Index of HTML Files</title>
</head>
<body>
    <h1>Index of HTML Files</h1>
    <ul>
"""
    footer = """
    </ul>
</body>
</html>
"""

    # List to store HTML links
    links = []

    # Traverse the directory and find HTML files
    for root, _, files in os.walk(directory):
        for file in files:
            if file.endswith('.html'):
                relative_path = os.path.relpath(
                    os.path.join(root, file), directory)
                links.append(
                    f'        <li><a href="{relative_path}">{relative_path}</a></li>')

    # Generate the full HTML content
    content = header + "\n".join(links) + footer

    # Write the content to index.html
    with open(os.path.join(directory, 'index.html'), 'w', encoding='utf-8') as f:
        f.write(content)


# Usage
directory_path = 'rules'  # Replace with your directory path
generate_index_html(directory_path)

In [9]:
import os
from llama_index.readers.file import HTMLTagReader

reader = HTMLTagReader(tag="body")

# sample_data 폴더의 경로를 지정합니다.
sample_data_path = './data/'

# sample_data 폴더에 있는 모든 파일 중에서 HTML 확장자를 가진 파일을 찾습니다.
html_files = [f for f in os.listdir(sample_data_path) if f.endswith('.html')]

docs = []
# HTML 파일 목록을 출력합니다.
print("HTML 파일 목록 (상대 경로):")
for html_file in html_files:
  try:
    relative_path = os.path.join('data', html_file)
    print(relative_path)
    html_data = reader.load_data(relative_path)
    print(html_data)
    docs.append(html_data)
  except:
    print("Somthng wrong")



HTML 파일 목록 (상대 경로):
data/Gku (95).html
[Document(id_='ba2d4fb2-b2a3-406f-862e-5500f546256e', embedding=None, metadata={'tag': 'body', 'tag_id': None, 'file_path': 'data/Gku (95).html'}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, text='HOME < 본부,부속기관 및 부속 연구소 < 본부 및 부속 기관 < 결혼·다출산문화운동센터 운영규정\xa0\xa0\xa0|\xa0\xa0\xa0[프린트하기]\n\n\n\n\n\n결혼·다출산문화운동센터 운영규정\n\t\n\n\t소관부서 : 결혼·다출산문화운동센터 1451\n\t\n\n\n\n\n\n\t\t\t\t제정 2019. 5. 8 규정 제259호\n\t\t\t\t\n\n\n\n\n\n\t\t\t\t개정 2019. 10. 04 규정 제266호\n\t\t\t\t\n\n\n\n\n\n|  \n부 칙 | \n\n\n제 1 조 (목적) \n\t\t\t\n\n \n\n\n이 규정은 한동대학교(이하 ‘이 대학교’라 한다) 결혼·다출산문화 운동센터(이하 \'센터\'라 한다.)의 조직과 운영에 관하여 필요한 사항을 규정함을 목적으로 한다.\n\t\t\t\n\n제 2 조 (정의) \n\t\t\t\n\n \n\n\n센터는 이 대학교의 교직원과 학생들의 다출산을 장려하고 결혼, 임신, 출산, 육아의 과정에서 필요한 도움을 지원하며 이를 위한 인프라를 조성하여 문화지대를 형성하고 더 나아가 한국의 기독교계와 사회 일반에 확산하는 일을 추진하기 위한 조직을 말한다.\n\t\t\t\n\n제 3 조 (사업) \n\t\t\t\n\n \n\n\n센터는 다음 각 호의 사업을 수행한다.\n1. 다출산, 건강가정 문화와 관련된 학술적인 연구와 용역 사업\n2. 다출산, 건강가정 문화와 관련된 세계관과 의식 변화

In [10]:
[doc[0].text for doc in docs]

['HOME < 본부,부속기관 및 부속 연구소 < 본부 및 부속 기관 < 결혼·다출산문화운동센터 운영규정\xa0\xa0\xa0|\xa0\xa0\xa0[프린트하기]\n\n\n\n\n\n결혼·다출산문화운동센터 운영규정\n\t\n\n\t소관부서 : 결혼·다출산문화운동센터 1451\n\t\n\n\n\n\n\n\t\t\t\t제정 2019. 5. 8 규정 제259호\n\t\t\t\t\n\n\n\n\n\n\t\t\t\t개정 2019. 10. 04 규정 제266호\n\t\t\t\t\n\n\n\n\n\n|  \n부 칙 | \n\n\n제 1 조 (목적) \n\t\t\t\n\n \n\n\n이 규정은 한동대학교(이하 ‘이 대학교’라 한다) 결혼·다출산문화 운동센터(이하 \'센터\'라 한다.)의 조직과 운영에 관하여 필요한 사항을 규정함을 목적으로 한다.\n\t\t\t\n\n제 2 조 (정의) \n\t\t\t\n\n \n\n\n센터는 이 대학교의 교직원과 학생들의 다출산을 장려하고 결혼, 임신, 출산, 육아의 과정에서 필요한 도움을 지원하며 이를 위한 인프라를 조성하여 문화지대를 형성하고 더 나아가 한국의 기독교계와 사회 일반에 확산하는 일을 추진하기 위한 조직을 말한다.\n\t\t\t\n\n제 3 조 (사업) \n\t\t\t\n\n \n\n\n센터는 다음 각 호의 사업을 수행한다.\n1. 다출산, 건강가정 문화와 관련된 학술적인 연구와 용역 사업\n2. 다출산, 건강가정 문화와 관련된 세계관과 의식 변화를 위한 캠페인과 문화사역\n3. 학생과 교직원의 결혼, 임신, 출산, 육아와 관련된 인프라 조성 및 운영사업\n4. 이 대학교를 시범지대로 삼아 기독교 대학과 일반 대학에 창조적 가정문화를 확산하는 사업\n5. 기타 센터의 설립목적 달성을 위해 필요한 사업\n\t\t\t\n\n제 4 조 (조직 및 구성) \n\t\t\t\n\n \n\n\n① 센터에는 센터장을 두며, 센터장은 조교수 이상의 교원 중에서 총장이 임명하고 임기는 2년으로 하되 연임할 수 있다. \n② 센터장은 센터의 업

### Chroma DB setting

In [ ]:
pip install chromadb

In [ ]:
pip install llama-index-vector-stores-chroma

크로마 인덱스 생성하기

In [ ]:
pip install llama-index-embeddings-openai


In [ ]:
pip install llama-index-llms-openai

In [ ]:
# import
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader
from llama_index.vector_stores.chroma import ChromaVectorStore
from llama_index.core import StorageContext
from IPython.display import Markdown, display
import chromadb

# set up OpenAI
import os
import openai
from google.colab import userdata

OPENAI_API_KEY = ""
openai.api_key = userdata.get('OPENAI_API_KEY')
os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY

from llama_index.core import Settings

# LLM (gpt-3.5-turbo)
Settings.llm = OpenAI(temperature=0, model="gpt-3.5-turbo")
Settings.chunk_size = 4098


In [ ]:
# create client and a new collection
chroma_client = chromadb.EphemeralClient()
chroma_collection = chroma_client.get_or_create_collection("hgu_rules_text-embedding-3-small")


# get API key and create embeddings
from llama_index.embeddings.openai import OpenAIEmbedding

embed_model = OpenAIEmbedding(model="text-embedding-3-small")

# load documents
documents = [doc[0] for doc in docs]

# set up ChromaVectorStore and load in data
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)
storage_context = StorageContext.from_defaults(vector_store=vector_store)
index = VectorStoreIndex.from_documents(
    documents, storage_context=storage_context, embed_model=embed_model
)

In [ ]:

def fetch_chromadb_contents():
    # 데이터베이스에 저장된 내용 조회
    db_contents = chroma_collection.get()
    existing_count = chroma_collection.count()
    print(existing_count)
    batch_size = 1

    batch = chroma_collection.get(
        include=["documents"],
        limit=batch_size,
        offset=0)
    print(batch['documents'][0])  # do something with the batch


    # for i in range(0, existing_count, batch_size):
    #     batch = chroma_collection.get(
    #         include=["metadatas", "documents"],
    #         limit=batch_size,
    #         offset=i)
    #     print(batch)  # do something with the batch

    # # 조회된 데이터를 리스트로 변환
    # data_list = [item for item in db_contents]

    # return data_list

fetch_chromadb_contents()

In [ ]:
# set up ChromaVectorStore and load in data
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)
storage_context = StorageContext.from_defaults(vector_store=vector_store)
index = VectorStoreIndex.from_documents(
    documents, storage_context=storage_context, embed_model=embed_model
)

In [ ]:
# Query Data
query_engine = index.as_query_engine()
q = "학생이 학교 차량을 운행할 수 있는가?"
result = query_engine.retrieve(q)
response = query_engine.query(q + " 규정집의 제목과 해당하는 조, 항을 함께 표시해줘. 한글로 대답해줘")
display(Markdown(f"<b>{result}</b><p/><b>{response}</b>"))

### Reranker 추가하기

In [ ]:
import nest_asyncio

nest_asyncio.apply()


In [ ]:
import logging
import sys

logging.basicConfig(stream=sys.stdout, level=logging.INFO)
logging.getLogger().addHandler(logging.StreamHandler(stream=sys.stdout))
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader
from llama_index.core.postprocessor import LLMRerank
from llama_index.llms.openai import OpenAI
from IPython.display import Markdown, display

In [ ]:
from llama_index.core.retrievers import VectorIndexRetriever
from llama_index.core import QueryBundle
import pandas as pd
from IPython.display import display, HTML


# pd.set_option("display.max_colwidth", -1)


def get_retrieved_nodes(
    query_str, vector_top_k=10, reranker_top_n=3, with_reranker=False
):
    query_bundle = QueryBundle(query_str)
    # configure retriever
    retriever = VectorIndexRetriever(
        index=index,
        similarity_top_k=vector_top_k,
    )
    retrieved_nodes = retriever.retrieve(query_bundle)

    if with_reranker:
        # configure reranker
        reranker = LLMRerank(
            choice_batch_size=5,
            top_n=reranker_top_n,
        )
        retrieved_nodes = reranker.postprocess_nodes(
            retrieved_nodes, query_bundle
        )

    return retrieved_nodes


def pretty_print(df):
    return display(HTML(df.to_html().replace("\\n", "")))


def visualize_retrieved_nodes(nodes) -> None:
    result_dicts = []
    for node in nodes:
        result_dict = {"Score": node.score, "Text": node.node.get_text()}
        result_dicts.append(result_dict)

    pretty_print(pd.DataFrame(result_dicts))

In [ ]:
new_nodes = get_retrieved_nodes(
    "학생이 차량을 운행할 수 있는가?",
    vector_top_k=10,
    reranker_top_n=3,
    with_reranker=True,
)

visualize_retrieved_nodes(new_nodes)

In [ ]:

query_engine = index.as_query_engine(
    similarity_top_k=10,
    node_postprocessors=[
        LLMRerank(
            choice_batch_size=5,
            top_n=2,
        )
    ],
    response_mode="tree_summarize",
)

In [ ]:
response = query_engine.query(
    "학교차량을 학생이 운영할 수 있나?",
)
display(Markdown(f"<b>{response}</b>"))


### HyDE 추가

In [ ]:
from llama_index.core.indices.query.query_transform import HyDEQueryTransform
from llama_index.core.query_engine import TransformQueryEngine

In [ ]:
hyde = HyDEQueryTransform(include_original=True)
hyde_query_engine = TransformQueryEngine(query_engine, hyde)
print(hyde_query_engine.retrieve("인공지능 센터의 설립 목적은? 한국어로 근거와 함께 대답해줘"))
response = hyde_query_engine.query("인공지능 센터의 설립 목적은? 한국어로 근거와 함께 대답해줘")
display(Markdown(f"<b>{response}</b>"))

In [ ]:
# Query Data
query_engine = hyde_query_engine
q = "학생이 학교 차량을 운행할 수 있는가?"
prompts = query_engine.get_prompts()
result = query_engine.retrieve(q)
response = query_engine.query(q + " 규정집의 제목과 해당하는 조, 항을 함께 표시해줘. 한글로 대답해줘")
display(Markdown(f"<p>{result}</p><p>{prompts}</p><p/><b>{response}</b>"))